In [1]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
from apyori import apriori

In [2]:
pd.options.display.float_format = '{:,.4f}'.format
np.set_printoptions(precision=4)
plt.rcParams['font.sans-serif'] = 'SimHei'
plt.rcParams['axes.unicode_minus'] = False

In [3]:
test_file = "resource/400_data.xlsx"
data = pd.read_excel(test_file)
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 116 entries, 0 to 115
Data columns (total 19 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   序号         116 non-null    int64 
 1   反馈时间       116 non-null    int64 
 2   顾客来源       116 non-null    object
 3   渠道         116 non-null    object
 4   顾客名称/顾客ID  116 non-null    object
 5   联系方式       115 non-null    object
 6   反馈属性       116 non-null    object
 7   品牌         116 non-null    object
 8   所购产品       116 non-null    object
 9   制造批号       116 non-null    object
 10  规格         116 non-null    object
 11  顾客反馈内容     116 non-null    object
 12  回复内容       116 non-null    object
 13  一级分类       116 non-null    object
 14  二级分类       116 non-null    object
 15  反馈部门       116 non-null    object
 16  是否已完成      116 non-null    object
 17  情感分析       116 non-null    object
 18  分词内容       116 non-null    object
dtypes: int64(2), object(17)
memory usage: 17.3+ KB


In [4]:
data['分词内容'] = data['分词内容'].apply(lambda x: x[1:].split(','))
data['分词内容']

0      [客户, 疑似, 假货, 举报, 抖, 音, 平台, 店铺, 原, 名称, 小杨, 甄选, ...
1                     [客户, 来电, 未, 接到, 回复, 多次, 均, 无人, 接听]
2      [客户, 告知, 拼多多, 店铺, 傲美, 家居, 专营店, 购买, 惠润, 洗发水, 有,...
3      [客户, 告知, 需要, 采购, 菲, 婷, 丝, 产品, 浙江, 杭州, 地区, 怎么, 联系]
4      [客户, 来电, 告知, 李可容, 委托, 律师, 关于, 李可容, 售卖, 芬, 浓, 假...
                             ...                        
111    [客户, 告知, 拼多多, 日, 淘, 优选, 海外, 专营店, 购买, 一瓶, 吾诺, 保...
112    [客户, 告知, 拼多多, LUOXI, 海外, 专营店, 购买, 一瓶, 吾诺, 洗面奶,...
113       [客户, 告知, 上海, 一家, 贸易公司, 需要, 采购, 吾诺, 产品, 怎么, 联系]
114    [客户, 告知, 新浪网, 投诉, 处理, 中心, 今天, 接到, 一起, 投诉, 我, 司...
115    [客户, 告知, 需要, 采购, 大约, 600, 瓶, 惠润, 洗发水, 和, 沐浴露, ...
Name: 分词内容, Length: 116, dtype: object

In [5]:
data_list = list(data['分词内容'])
data_list[:5]

[['客户',
  '疑似',
  '假货',
  '举报',
  '抖',
  '音',
  '平台',
  '店铺',
  '原',
  '名称',
  '小杨',
  '甄选',
  '日用',
  '好',
  '物',
  '后',
  '更名',
  '为',
  '云顶',
  '日用',
  '购买',
  '可悠然',
  '沐浴露',
  '怀疑',
  '假货',
  '要求',
  '公司',
  '打假',
  '可以',
  '把',
  '自己',
  '购买',
  '产品',
  '邮寄',
  '给',
  '公司',
  '这边',
  '鉴定',
  '客户',
  '已',
  '提供',
  '购买',
  '记录',
  '及',
  '产品',
  '正反面',
  '底面',
  '图片'],
 ['客户', '来电', '未', '接到', '回复', '多次', '均', '无人', '接听'],
 ['客户',
  '告知',
  '拼多多',
  '店铺',
  '傲美',
  '家居',
  '专营店',
  '购买',
  '惠润',
  '洗发水',
  '有',
  '胶水',
  '味',
  '臭味',
  '怀疑',
  '假货',
  '但是',
  '店铺',
  '告知',
  '授权',
  '店铺',
  '想',
  '要',
  '辨别',
  '真伪'],
 ['客户', '告知', '需要', '采购', '菲', '婷', '丝', '产品', '浙江', '杭州', '地区', '怎么', '联系'],
 ['客户',
  '来电',
  '告知',
  '李可容',
  '委托',
  '律师',
  '关于',
  '李可容',
  '售卖',
  '芬',
  '浓',
  '假货',
  '分销',
  '上海',
  '北京',
  '等',
  '地',
  '数量',
  '大概',
  '2万',
  '瓶',
  '案件',
  '地',
  '上海',
  '想',
  '要',
  '联系',
  '法务',
  '负责人',
  '沟通',
  '寻求',
  '谅解']]

In [ ]:
results = apriori(data_list, min_support=0.03, min_confidence=0.4)
df=pd.DataFrame()
# 遍历结果数据
lis1=[];lis2=[];lis3=[];lis4=[]
for result in results:
    # 获取支持度,并保留3位小数
    support = round(result.support, 3)
    # 遍历ordered_statistics对象
    for rule in result.ordered_statistics:
        # 获取前件和后件并转成列表
        head_set = list(rule.items_base)
        tail_set = list(rule.items_add)
        # 跳过前件为空的数据
        if head_set == []:
                continue
        # 将前件、后件拼接成关联规则的形式
        related_catogory = str(head_set)+'→'+str(tail_set)
        # 提取置信度，并保留3位小数
        confidence = round(rule.confidence, 3)
        # 提取提升度，并保留3位小数
        lift = round(rule.lift, 3)
        # 查看强关联规则，支持度，置信度，提升度
        print(related_catogory, support, confidence, lift)
        lis1.append(related_catogory);lis2.append(support)
        lis3.append(confidence);lis4.append(lift)

[':']→['客户'] 0.043 1.0 1.036
['一家']→['一批'] 0.086 0.625 3.152
['一批']→['一家'] 0.086 0.435 3.152
['一家']→['产品'] 0.086 0.625 1.611
['一家']→['企业'] 0.086 0.625 5.577
['企业']→['一家'] 0.086 0.769 5.577
['一家']→['司'] 0.06 0.438 2.03
['一家']→['告知'] 0.138 1.0 1.275
['一家']→['客户'] 0.138 1.0 1.036
['一家']→['怎么'] 0.129 0.938 2.417
['一家']→['联系'] 0.129 0.938 2.219
['贵']→['一家'] 0.043 0.455 3.295
['一家']→['采购'] 0.112 0.812 2.356
['一家']→['需要'] 0.103 0.75 1.851
['一批']→['产品'] 0.155 0.783 2.017
['产品']→['一批'] 0.155 0.4 2.017
['企业']→['一批'] 0.078 0.692 3.492
['一批']→['告知'] 0.198 1.0 1.275
['一批']→['地区'] 0.095 0.478 2.312
['地区']→['一批'] 0.095 0.458 2.312
['一批']→['客户'] 0.198 1.0 1.036
['一批']→['怎么'] 0.198 1.0 2.578
['怎么']→['一批'] 0.198 0.511 2.578
['一批']→['洗护'] 0.103 0.522 4.035
['洗护']→['一批'] 0.103 0.8 4.035
['一批']→['联系'] 0.198 1.0 2.367
['联系']→['一批'] 0.198 0.469 2.367
['一批']→['采购'] 0.19 0.957 2.774
['采购']→['一批'] 0.19 0.55 2.774
['一批']→['需要'] 0.198 1.0 2.468
['需要']→['一批'] 0.198 0.489 2.468
['一瓶']→['告知'] 0.086 1.0 1.275
['一瓶']→

['一家']→['产品', '一批'] 0.069 0.5 3.222
['一家', '一批']→['产品'] 0.069 0.8 2.062
['一家', '产品']→['一批'] 0.069 0.8 4.035
['产品', '一批']→['一家'] 0.069 0.444 3.222
['企业']→['一家', '一批'] 0.052 0.462 5.354
['一家', '一批']→['企业'] 0.052 0.6 5.354
['企业', '一家']→['一批'] 0.052 0.6 3.026
['企业', '一批']→['一家'] 0.052 0.667 4.833
['司', '一家']→['一批'] 0.034 0.571 2.882
['司', '一批']→['一家'] 0.034 0.667 4.833
['一家']→['一批', '告知'] 0.086 0.625 3.152
['一批']→['一家', '告知'] 0.086 0.435 3.152
['一家', '一批']→['告知'] 0.086 1.0 1.275
['一家', '告知']→['一批'] 0.086 0.625 3.152
['告知', '一批']→['一家'] 0.086 0.435 3.152
['一家']→['客户', '一批'] 0.086 0.625 3.152
['一批']→['客户', '一家'] 0.086 0.435 3.152
['一家', '一批']→['客户'] 0.086 1.0 1.036
['客户', '一家']→['一批'] 0.086 0.625 3.152
['客户', '一批']→['一家'] 0.086 0.435 3.152
['一家']→['怎么', '一批'] 0.086 0.625 3.152
['一批']→['怎么', '一家'] 0.086 0.435 3.362
['一家', '一批']→['怎么'] 0.086 1.0 2.578
['怎么', '一家']→['一批'] 0.086 0.667 3.362
['怎么', '一批']→['一家'] 0.086 0.435 3.152
['一家', '一批']→['洗护'] 0.052 0.6 4.64
['一家', '洗护']→['一批'] 0.052 1.0 5.0

['一家', '一批']→['企业', '产品'] 0.043 0.5 8.286
['一家', '产品']→['企业', '一批'] 0.043 0.5 6.444
['企业', '一家']→['产品', '一批'] 0.043 0.5 3.222
['企业', '一批']→['一家', '产品'] 0.043 0.556 6.444
['企业', '产品']→['一家', '一批'] 0.043 0.714 8.286
['一家', '一批', '产品']→['企业'] 0.043 0.625 5.577
['企业', '一家', '一批']→['产品'] 0.043 0.833 2.148
['企业', '一家', '产品']→['一批'] 0.043 0.833 4.203
['企业', '产品', '一批']→['一家'] 0.043 0.833 6.042
['司', '一家']→['产品', '一批'] 0.034 0.571 3.683
['司', '一批']→['一家', '产品'] 0.034 0.667 7.733
['一家', '一批', '产品']→['司'] 0.034 0.5 2.32
['司', '一家', '一批']→['产品'] 0.034 1.0 2.578
['司', '一家', '产品']→['一批'] 0.034 0.8 4.035
['司', '产品', '一批']→['一家'] 0.034 0.667 4.833
['一家']→['一批', '产品', '告知'] 0.069 0.5 3.222
['一家', '一批']→['产品', '告知'] 0.069 0.8 2.442
['一家', '产品']→['一批', '告知'] 0.069 0.8 4.035
['一家', '告知']→['产品', '一批'] 0.069 0.5 3.222
['产品', '一批']→['一家', '告知'] 0.069 0.444 3.222
['一家', '一批', '产品']→['告知'] 0.069 1.0 1.275
['告知', '一家', '一批']→['产品'] 0.069 0.8 2.062
['一家', '告知', '产品']→['一批'] 0.069 0.8 4.035
['告知', '产品', '一批']→['

['价', '想', '合作']→['电商'] 0.034 1.0 16.571
['电商', '价', '合作']→['想'] 0.034 1.0 5.273
['电商', '价', '想']→['合作'] 0.034 1.0 14.5
['电商', '想', '合作']→['价'] 0.034 1.0 29.0
['价']→['合作', '维权', '想'] 0.034 1.0 29.0
['合作']→['价', '维权', '想'] 0.034 0.5 14.5
['维权']→['价', '想', '合作'] 0.034 1.0 29.0
['价', '合作']→['维权', '想'] 0.034 1.0 29.0
['价', '想']→['维权', '合作'] 0.034 1.0 29.0
['价', '维权']→['想', '合作'] 0.034 1.0 16.571
['想', '合作']→['价', '维权'] 0.034 0.571 16.571
['维权', '合作']→['价', '想'] 0.034 1.0 29.0
['想', '维权']→['价', '合作'] 0.034 1.0 29.0
['价', '想', '合作']→['维权'] 0.034 1.0 29.0
['价', '维权', '合作']→['想'] 0.034 1.0 5.273
['价', '想', '维权']→['合作'] 0.034 1.0 14.5
['维权', '想', '合作']→['价'] 0.034 1.0 29.0
['价']→['要', '想', '合作'] 0.034 1.0 16.571
['合作']→['要', '价', '想'] 0.034 0.5 14.5
['价', '合作']→['要', '想'] 0.034 1.0 5.273
['价', '想']→['要', '合作'] 0.034 1.0 16.571
['要', '价']→['想', '合作'] 0.034 1.0 16.571
['想', '合作']→['要', '价'] 0.034 0.571 16.571
['要', '合作']→['价', '想'] 0.034 0.571 16.571
['价', '想', '合作']→['要'] 0.034 1.0 4.462
['要', '

['霖']→['客户', '怎么', '告知'] 0.034 0.667 1.758
['霖', '告知']→['客户', '怎么'] 0.034 0.8 2.062
['客户', '霖']→['怎么', '告知'] 0.034 0.667 1.758
['霖', '怎么']→['客户', '告知'] 0.034 1.0 1.289
['客户', '霖', '告知']→['怎么'] 0.034 0.8 2.062
['霖', '怎么', '告知']→['客户'] 0.034 1.0 1.036
['客户', '霖', '怎么']→['告知'] 0.034 1.0 1.275
['控']→['客户', '想', '告知'] 0.034 1.0 5.273
['控', '告知']→['客户', '想'] 0.034 1.0 5.273
['客户', '控']→['想', '告知'] 0.034 1.0 5.273
['想', '控']→['客户', '告知'] 0.034 1.0 1.289
['控', '客户', '告知']→['想'] 0.034 1.0 5.273
['控', '想', '告知']→['客户'] 0.034 1.0 1.036
['客户', '想', '控']→['告知'] 0.034 1.0 1.275
['方向']→['客户', '想', '告知'] 0.043 1.0 5.273
['告知', '方向']→['客户', '想'] 0.043 1.0 5.273
['客户', '方向']→['想', '告知'] 0.043 1.0 5.273
['想', '方向']→['客户', '告知'] 0.043 1.0 1.289
['客户', '告知', '方向']→['想'] 0.043 1.0 5.273
['想', '告知', '方向']→['客户'] 0.043 1.0 1.036
['客户', '想', '方向']→['告知'] 0.043 1.0 1.275
['有']→['客户', '想', '告知'] 0.052 0.462 2.434
['有', '告知']→['客户', '想'] 0.052 0.545 2.876
['客户', '有']→['想', '告知'] 0.052 0.462 2.434
['想', '有']→['客户'

...

23.2
['图片', '购买']→['店铺', '假货', '正反面', '记录'] 0.034 0.8 23.2
['店铺', '正反面']→['记录', '购买', '假货', '图片'] 0.034 1.0 29.0
['店铺', '记录']→['图片', '购买', '假货', '正反面'] 0.034 1.0 29.0
['记录', '正反面']→['店铺', '购买', '假货', '图片'] 0.034 0.8 23.2
['正反面', '购买']→['店铺', '假货', '记录', '图片'] 0.034 0.8 23.2
['记录', '购买']→['店铺', '正反面', '假货', '图片'] 0.034 0.8 23.2
['图片', '假货', '店铺']→['记录', '购买', '正反面'] 0.034 1.0 23.2
['图片', '假货', '正反面']→['店铺', '购买', '记录'] 0.034 1.0 29.0
['图片', '假货', '记录']→['店铺', '购买', '正反面'] 0.034 1.0 29.0
['图片', '假货', '购买']→['店铺', '正反面', '记录'] 0.034 1.0 29.0
['店铺', '假货', '正反面']→['记录', '购买', '图片'] 0.034 1.0 23.2
['店铺', '假货', '记录']→['图片', '购买', '正反面'] 0.034 1.0 23.2
['店铺', '假货', '购买']→['记录', '正反面', '图片'] 0.034 0.571 13.257
['记录', '假货', '正反面']→['店铺', '购买', '图片'] 0.034 1.0 29.0
['假货', '购买', '正反面']→['店铺', '记录', '图片'] 0.034 1.0 29.0
['记录', '假货', '购买']→['店铺', '正反面', '图片'] 0.034 1.0 29.0
['图片', '正反面', '店铺']→['记录', '购买', '假货'] 0.034 1.0 29.0
['图片', '店铺', '记录']→['购买', '假货', '正反面'] 0.034 1.0 29.0
['图片', '购买', '店铺']→

['图片', '及', '已']→['店铺', '正反面', '提供'] 0.034 1.0 29.0
['图片', '及', '店铺']→['正反面', '提供', '已'] 0.034 1.0 29.0
['图片', '及', '提供']→['店铺', '正反面', '已'] 0.034 0.8 23.2
['图片', '正反面', '及']→['店铺', '提供', '已'] 0.034 0.8 23.2
['店铺', '及', '已']→['图片', '正反面', '提供'] 0.034 1.0 23.2
['及', '提供', '已']→['店铺', '正反面', '图片'] 0.034 1.0 29.0
['正反面', '及', '已']→['店铺', '提供', '图片'] 0.034 1.0 29.0
['店铺', '及', '提供']→['图片', '正反面', '已'] 0.034 1.0 29.0
['店铺', '正反面', '及']→['图片', '提供', '已'] 0.034 1.0 29.0
['正反面', '及', '提供']→['店铺', '已', '图片'] 0.034 0.8 23.2
['图片', '店铺', '已']→['正反面', '及', '提供'] 0.034 1.0 23.2
['图片', '提供', '已']→['店铺', '正反面', '及'] 0.034 1.0 29.0
['图片', '正反面', '已']→['店铺', '及', '提供'] 0.034 1.0 29.0
['图片', '店铺', '提供']→['正反面', '及', '已'] 0.034 1.0 29.0
['图片', '正反面', '店铺']→['及', '提供', '已'] 0.034 1.0 29.0
['图片', '正反面', '提供']→['店铺', '及', '已'] 0.034 0.8 23.2
['店铺', '提供', '已']→['图片', '正反面', '及'] 0.034 1.0 23.2
['店铺', '正反面', '已']→['图片', '及', '提供'] 0.034 1.0 23.2
['正反面', '提供', '已']→['店铺', '及', '图片'] 0.034 1.0 29.0
['店铺', '正反面'

['可']→['告知', '联系', '润', '怎么', '护手霜'] 0.034 0.667 19.333
['护手霜']→['告知', '可', '联系', '润', '怎么'] 0.034 0.571 16.571
['润']→['告知', '可', '联系', '怎么', '护手霜'] 0.034 0.667 19.333
['可', '告知']→['护手霜', '润', '联系', '怎么'] 0.034 0.8 23.2
['可', '怎么']→['润', '联系', '护手霜', '告知'] 0.034 1.0 29.0
['可', '护手霜']→['润', '联系', '怎么', '告知'] 0.034 0.8 23.2
['润', '可']→['护手霜', '联系', '怎么', '告知'] 0.034 0.667 15.467
['可', '联系']→['润', '护手霜', '怎么', '告知'] 0.034 1.0 29.0
['护手霜', '告知']→['润', '可', '联系', '怎么'] 0.034 0.667 19.333
['润', '告知']→['护手霜', '可', '联系', '怎么'] 0.034 0.8 23.2
['护手霜', '怎么']→['润', '可', '联系', '告知'] 0.034 0.8 23.2
['润', '怎么']→['可', '联系', '护手霜', '告知'] 0.034 1.0 29.0
['润', '护手霜']→['可', '联系', '怎么', '告知'] 0.034 0.8 23.2
['联系', '护手霜']→['润', '可', '怎么', '告知'] 0.034 0.8 23.2
['润', '联系']→['可', '护手霜', '怎么', '告知'] 0.034 1.0 29.0
['可', '怎么', '告知']→['润', '联系', '护手霜'] 0.034 1.0 29.0
['可', '护手霜', '告知']→['润', '联系', '怎么'] 0.034 1.0 29.0
['润', '可', '告知']→['护手霜', '联系', '怎么'] 0.034 0.8 18.56
['可', '联系', '告知']→['润', '护手霜', '怎么'] 0.034 

['客户', '洗护']→['司', '联系', '采购', '告知'] 0.06 0.467 6.767
['联系', '洗护']→['司', '客户', '采购', '告知'] 0.06 0.467 6.767
['采购', '洗护']→['司', '客户', '联系', '告知'] 0.06 0.5 4.462
['司', '告知', '洗护']→['客户', '联系', '采购'] 0.06 0.875 2.603
['司', '联系', '告知']→['客户', '采购', '洗护'] 0.06 0.538 4.462
['司', '采购', '告知']→['客户', '联系', '洗护'] 0.06 0.875 6.767
['司', '客户', '洗护']→['联系', '采购', '告知'] 0.06 0.875 2.603
['司', '客户', '联系']→['采购', '告知', '洗护'] 0.06 0.538 4.462
['司', '客户', '采购']→['联系', '告知', '洗护'] 0.06 0.875 6.767
['司', '联系', '洗护']→['客户', '采购', '告知'] 0.06 0.875 2.537
['司', '采购', '洗护']→['客户', '联系', '告知'] 0.06 1.0 2.367
['司', '联系', '采购']→['客户', '告知', '洗护'] 0.06 0.875 6.767
['客户', '告知', '洗护']→['司', '联系', '采购'] 0.06 0.467 6.767
['联系', '告知', '洗护']→['司', '客户', '采购'] 0.06 0.467 6.767
['采购', '告知', '洗护']→['司', '客户', '联系'] 0.06 0.5 4.462
['客户', '联系', '洗护']→['司', '采购', '告知'] 0.06 0.467 6.767
['客户', '采购', '洗护']→['司', '联系', '告知'] 0.06 0.5 4.462
['联系', '采购', '洗护']→['司', '客户', '告知'] 0.06 0.5 3.222
['司', '客户', '告知', '洗护']→['联系', '采购'] 0

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

